<a href="https://colab.research.google.com/github/AliaksandrSiarohin/articulated-animation/blob/main/demo.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [9]:
import warnings
warnings.filterwarnings("ignore")

import os
os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"   
os.environ["CUDA_VISIBLE_DEVICEurlS"]="1"
from demo import make_animation
from skimage import img_as_ubyte

In [10]:
from demo import load_checkpoints

import imageio
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from skimage.transform import resize
from skimage.color import rgba2rgb
from IPython.display import HTML
import warnings

from preprocessing_davis import crop_video_using_path

from preprocessing_davis import *

from preprocessing_davis import display_video
from preprocessing_davis import mask_image
from preprocessing_davis import bbox2squared

**Load checkpoints.**

In [16]:
model_checkpoint=os.path.join('checkpoints', 'davis384_human_plus_taichi_avd.pth')

# model_checkpoint2=os.path.join(model_dir, '00000027-cpk-avd.pth')

In [17]:
def pad_white(im): # im : imageio.imread로 읽은...
    im_array=np.array(im)
    h,w=im_array.shape[:2]
    pad_length=abs(w-h)  
    if w>h:
        upper=np.full((pad_length//2, w, 3),255).astype('uint8')
        lower=np.full((pad_length-pad_length//2, w, 3), 255).astype('uint8')
        return imageio.core.util.Image(np.concatenate([upper, im_array, lower], axis=0))
    else:
        left=np.full((h,pad_length//2, 3),255).astype('uint8')
        right=np.full((h,pad_length-pad_length//2, 3),255).astype('uint8')

        return imageio.core.util.Image(np.concatenate([left, im_array, right], axis=1))
   

In [18]:
def rgba2rgb( rgba, background=(255,255,255) ):
    row, col, ch = rgba.shape

    if ch == 3:
        return rgba

    assert ch == 4, 'RGBA image has 4 channels.'

    rgb = np.zeros( (row, col, 3), dtype='float32' )
    r, g, b, a = rgba[:,:,0], rgba[:,:,1], rgba[:,:,2], rgba[:,:,3]

    a = np.asarray( a, dtype='float32' ) / 255.0

    R, G, B = background

    rgb[:,:,0] = r * a + (1.0 - a) * R
    rgb[:,:,1] = g * a + (1.0 - a) * G
    rgb[:,:,2] = b * a + (1.0 - a) * B

    return np.asarray( rgb, dtype='uint8' )

In [19]:
def display(source, driving, generated=None, save=False):
    fig = plt.figure(figsize=(8 + 4 * (generated is not None), 6))

    ims = []
    for i in range(len(driving)):
        cols = [source]
        cols.append(driving[i])
        if generated is not None:
            cols.append(generated[i])
        im = plt.imshow(np.concatenate(cols, axis=1), animated=True)
        plt.axis('off')
        ims.append([im])
    if save==True:
        return ims
    ani = animation.ArtistAnimation(fig, ims, interval=50, repeat_delay=1000)
    plt.close()
    return ani

#### Using davis(only training)

In [20]:
generator, region_predictor, avd_network = load_checkpoints(config_path='config/davis384_human_plus_taichi.yaml',
                                                            checkpoint_path=model_checkpoint)

In [22]:
os.mkdir('tobigs_test')

In [23]:
url='https://media1.tenor.com/images/b6d81b8f62d840e986f80acbd11b2954/tenor.gif?itemid=18194446'
os.system("curl " + url + "> tobigs_test/test.gif")

url='https://img.dmitory.com/img/201810/6d1/qxm/6d1qxmdXEIamYoam4QeaYy.jpg'
os.system("curl " + url + "> tobigs_test/test.png")

source_image=imageio.imread('tobigs_test/test.png')
driving_video=imageio.mimread('tobigs_test/test.gif')

source_image = resize(source_image, (384, 384))[..., :3]
driving_video = [resize(frame, (384, 384))[..., :3] for frame in driving_video]

In [24]:
predictions = make_animation(source_image, driving_video, generator, 
                              region_predictor, avd_network, animation_mode='avd')

#save resulting video
#imageio.mimsave('generated.mp4', [img_as_ubyte(frame) for frame in predictions])
#video can be downloaded from /content folder
HTML(display(source_image, driving_video, predictions).to_html5_video())

100%|██████████| 89/89 [00:03<00:00, 25.84it/s]


In [25]:
predictions = make_animation(source_image, driving_video, generator, 
                              region_predictor, avd_network, animation_mode='standard') #animation_mode='avd')

#save resulting video
#imageio.mimsave('generated.mp4', [img_as_ubyte(frame) for frame in predictions])
#video can be downloaded from /content folder

HTML(display(source_image, driving_video, predictions).to_html5_video())

100%|██████████| 89/89 [00:03<00:00, 27.56it/s]


In [26]:
predictions = make_animation(source_image, driving_video, generator, 
                              region_predictor, avd_network, animation_mode='relative') #animation_mode='avd')

#save resulting video
#imageio.mimsave('generated.mp4', [img_as_ubyte(frame) for frame in predictions])
#video can be downloaded from /content folder

HTML(display(source_image, driving_video, predictions).to_html5_video())

100%|██████████| 89/89 [00:03<00:00, 26.87it/s]


### 화이트 패딩

In [27]:
from PIL import Image

In [28]:
def pad_white(im): # im : imageio.imread로 읽은...
    im_array=np.array(im)
    h,w=im_array.shape[:2]
    pad_length=abs(w-h)  
    if w>h:
        upper=np.full((pad_length//2, w, 3),255).astype('uint8')
        lower=np.full((pad_length-pad_length//2, w, 3), 255).astype('uint8')
        return imageio.core.util.Image(np.concatenate([upper, im_array, lower], axis=0))
    else:
        left=np.full((h,pad_length//2, 3),255).astype('uint8')
        right=np.full((h,pad_length-pad_length//2, 3),255).astype('uint8')

        return imageio.core.util.Image(np.concatenate([left, im_array, right], axis=1))
   

In [29]:
url='https://lh3.googleusercontent.com/proxy/yVzU3nUM3uDlJ2FpKcLuNnHREKElSSGxREW1XWdgmjqBo2ZUrT4E9Hneeemtj7zYLoNeR7-JUiLZbHVnLHy35_ZVZMwS5Ty_ICYs5_aeiT_SxAaz-rRQ_lrO=s0-d'
os.system("curl " + url + "> tobigs_test/test.gif")

url='https://photo.coolenjoy.net/data/editor/1608/Bimg_20160816212033_tzaayhtu.jpg'
os.system("curl " + url + "> tobigs_test/test.png")



0

In [30]:
source_image=imageio.imread('tobigs_test/test.png')
driving_video=imageio.mimread('tobigs_test/test.gif')

In [31]:
source_image = resize(source_image, (384, 384))[..., :3]
driving_video = [resize(frame, (384, 384))[..., :3] for frame in driving_video]

In [32]:
predictions = make_animation(source_image, driving_video, generator, 
                              region_predictor, avd_network, animation_mode='standard') #animation_mode='avd')

#save resulting video
#imageio.mimsave('sample/agumon.mp4', [img_as_ubyte(frame) for frame in predictions])
#video can be downloaded from /content folder

HTML(display(source_image, driving_video, predictions).to_html5_video())

100%|██████████| 50/50 [00:01<00:00, 26.94it/s]


In [33]:
predictions = make_animation(source_image, driving_video, generator, 
                              region_predictor, avd_network, animation_mode='relative') #animation_mode='avd')

#save resulting video
#imageio.mimsave('sample/agumon.mp4', [img_as_ubyte(frame) for frame in predictions])
#video can be downloaded from /content folder

HTML(display(source_image, driving_video, predictions).to_html5_video())

100%|██████████| 50/50 [00:01<00:00, 26.75it/s]


In [34]:
predictions = make_animation(source_image, driving_video, generator, 
                              region_predictor, avd_network, animation_mode='avd') #animation_mode='avd')

#save resulting video
#imageio.mimsave('sample/agumon.mp4', [img_as_ubyte(frame) for frame in predictions])
#video can be downloaded from /content folder

HTML(display(source_image, driving_video, predictions).to_html5_video())

100%|██████████| 50/50 [00:01<00:00, 25.90it/s]


#### Using DAVIS_MODEL with other driving video

In [49]:
# for_save=display(source_image, driving_video, predictions, save=True)
# imageio.mimsave('sample/IU_working_davis_taichi_ted.mp4', [img_as_ubyte(frame) for frame in for_save])

# Using dataset

In [62]:
os.listdir(davis_dir)

['DAVIS-2017-test-challenge-480p',
 'DAVIS-2017-test-dev-480p',
 'DAVIS-2017-Unsupervised-trainval-480p',
 'DAVIS-2016-trainval-480p',
 'DAVIS-2019-Unsupervised-test-challenge-480p',
 'DAVIS-2019-Unsupervised-test-dev-480p',
 'DAVIS_MR_supervised',
 '.ipynb_checkpoints',
 'DAVIS_MR_masking',
 'DAVIS_MR_masking_human',
 'Untitled Folder 1',
 'DAVIS_only_DAVIS',
 'DAVIS_plus_taichi']

In [71]:

train1_dir=os.path.join(davis_dir, 'DAVIS-2017-Unsupervised-trainval-480p')
# #train2_dir=os.path.join(davis_dir, 'DAVIS-2016-trainval-480p')

train_anno_dir=os.path.join(train1_dir, sub_anno_dir)
train_image_dir=os.path.join(train1_dir, sub_image_dir)
# # os.mkdir('../../DAVIS/DAVIS_MR_masking')
# # os.mkdir(train_save_dir)
# # os.mkdir(test_save_dir)

## DAVIS

In [72]:
# url='https://photo.coolenjoy.net/data/editor/1608/Bimg_20160816212033_tzaayhtu.jpg' lindy-hop_3 or 5
# os.system("curl " + url + "> tobigs_test/test.png")

# url='https://i.pinimg.com/564x/10/bb/23/10bb2394a287d78963ed1cda7bd3ac1c.jpg'
# os.system("curl " + url + "> tobigs_test/test.png")

# url='http://file3.instiz.net/data/file3/2018/05/05/8/3/0/830f3090dde6647cd7c2a0e9bbca6c55.jpg'
# os.system("curl " + url + "> tobigs_test/test.png")

# url='https://previews.123rf.com/images/jalephoto/jalephoto1503/jalephoto150300596/37864715-%ED%9D%B0%EC%83%89-%EB%B0%B0%EA%B2%BD%EC%97%90-%EA%B3%A0%EB%A6%BD-%EB%90%9C-t-%EC%85%94%EC%B8%A0-%EC%8B%A0%EB%B9%84%ED%95%9C-%EC%96%BC%EA%B5%B4-%EB%A5%BC-%EC%9E%85%EA%B3%A0-%EC%A0%84%ED%98%95%EC%A0%81%EC%9D%B8-%EC%83%81%EB%B0%98%EC%8B%A0-%EB%82%A8%EC%9E%90-%EC%8B%A4%EB%A3%A8%EC%97%A3.jpg'
# os.system("curl " + url + "> tobigs_test/test.png")

url='https://en.pimg.jp/064/776/098/1/64776098.jpg'
os.system("curl " + url + "> tobigs_test/test.png")
source_image=imageio.imread('tobigs_test/test.png')

source_image = resize(source_image, (384, 384))[..., :3]


#### os.listdir(test_save_dir)

In [78]:
os.listdir(test_save_dir)

['100000#upside-down_2.mp4',
 '100001#walking_2.mp4',
 '100002#breakdance-flare_1.mp4',
 '100003#lindy-hop_3.mp4',
 '100004#lindy-hop_5.mp4',
 '100005#lCb5w6n8kPs#004451#004631.mp4',
 '100006#lCb5w6n8kPs#010150#010295.mp4',
 '100007#lCb5w6n8kPs#011879#012014.mp4',
 '100008#lCb5w6n8kPs#012081#012216.mp4',
 '100009#0Q914by5A98#010440#010764.mp4',
 '100010#mndSqTrxpts#000000#000175.mp4',
 '100011#mndSqTrxpts#002234#002406.mp4',
 '100012#mndSqTrxpts#002406#002550.mp4',
 '100013#mndSqTrxpts#002911#003105.mp4',
 '100014#mndSqTrxpts#003600#003794.mp4']

In [79]:
driving_video=[(plt.imread(im)) for im in glob(os.path.join(test_save_dir, '100004#lindy-hop_5.mp4', '*'))]

In [80]:
predictions = make_animation(source_image, driving_video, generator, 
                             region_predictor, avd_network, animation_mode='standard')#animation_mode='avd')

#save resulting video
# imageio.mimsave('sample/ironman.mp4', [img_as_ubyte(frame) for frame in predictions])
#video can be downloaded from /content folder



HTML(display(source_image, driving_video, predictions).to_html5_video())

100%|██████████| 73/73 [00:02<00:00, 27.79it/s]


In [81]:
predictions = make_animation(source_image, driving_video, generator, 
                             region_predictor, avd_network, animation_mode='relative')#animation_mode='avd')

#save resulting video
# imageio.mimsave('sample/ironman.mp4', [img_as_ubyte(frame) for frame in predictions])
#video can be downloaded from /content folder



HTML(display(source_image, driving_video, predictions).to_html5_video())

100%|██████████| 73/73 [00:02<00:00, 27.48it/s]


In [82]:
# for_save=display(source_image, driving_video, predictions, save=True)
# imageio.mimsave('sample/man_dance.mp4', [img_as_ubyte(frame) for frame in for_save]

In [113]:
# url='https://i.pinimg.com/564x/ed/48/85/ed48858c33761b73eca8f111f058b035.jpg'
# # url='http://www.kgirls.net/files/attach/images/214/557/136/6ea4b05b17f0d3f01e685d68ea6cc8d9.jpg'
# url='https://4.bp.blogspot.com/-qB2JVKgJfJw/WR1EwI4-zaI/AAAAAAABh5I/SoLzNj1MLcg_MPXSotqgkHiRrulne9_uACLcB/s1600/1_2.jpg'
# os.system("curl " + url + "> tobigs_test/test.png")
# source_image=imageio.imread('tobigs_test/test.png')

source_image=imageio.imread('1111.PNG')
#source_image=rgba2rgb(source_image)
source_image = resize(source_image[..., :3], (384, 384))
# source_image = resize(pad_white(source_image[..., :3]), (384, 384))

In [114]:
ex_list=[ '100063#rollerblade_1.mp4',
 '100065#schoolgirls_2.mp4',
 '100066#schoolgirls_3.mp4',
 '100067#schoolgirls_4.mp4']

In [124]:
dr_list=[]
st_list=[]
re_list=[]
for ex in ex_list:
    driving_video=[(plt.imread(im)) for im in glob(os.path.join(train_save_dir, ex, '*'))]
    dr_list.append(driving_video)
    predictions = make_animation(source_image, driving_video, generator, 
                                 region_predictor, avd_network, animation_mode='standard')#animation_mode='avd')
    st_list.append(predictions)
    predictions = make_animation(source_image, driving_video, generator, 
                             region_predictor, avd_network, animation_mode='relative')#animation_mode='avd')
    re_list.append(predictions)

In [138]:
idx=0

In [139]:
HTML(display(source_image, dr_list[idx], re_list[idx]).to_html5_video())

In [140]:
HTML(display(source_image, dr_list[idx], st_list[idx]).to_html5_video())

In [141]:
idx+=1

In [142]:
HTML(display(source_image, dr_list[idx], re_list[idx]).to_html5_video())

In [143]:
HTML(display(source_image, dr_list[idx], st_list[idx]).to_html5_video())


In [144]:
idx+=1

In [145]:
HTML(display(source_image, dr_list[idx], re_list[idx]).to_html5_video())

In [146]:
HTML(display(source_image, dr_list[idx], st_list[idx]).to_html5_video())


In [147]:
idx+=1

In [148]:
HTML(display(source_image, dr_list[idx], re_list[idx]).to_html5_video())

In [149]:
HTML(display(source_image, dr_list[idx], st_list[idx]).to_html5_video())


In [150]:
url='https://photo.coolenjoy.net/data/editor/1608/Bimg_20160816212033_tzaayhtu.jpg'
os.system("curl " + url + "> tobigs_test/test.png")



0

In [151]:
source_image=imageio.imread('tobigs_test/test.png')

In [152]:
source_image = resize(source_image, (384, 384))[..., :3]

In [153]:
dr_list=[]
st_list=[]
re_list=[]
for ex in ex_list:
    driving_video=[(plt.imread(im)) for im in glob(os.path.join(train_save_dir, ex, '*'))]
    dr_list.append(driving_video)
    predictions = make_animation(source_image, driving_video, generator, 
                                 region_predictor, avd_network, animation_mode='standard')#animation_mode='avd')
    st_list.append(predictions)
    predictions = make_animation(source_image, driving_video, generator, 
                             region_predictor, avd_network, animation_mode='relative')#animation_mode='avd')
    re_list.append(predictions)

100%|██████████| 80/80 [00:02<00:00, 28.55it/s]


In [154]:
idx=0

In [155]:
HTML(display(source_image, dr_list[idx], re_list[idx]).to_html5_video())

In [156]:
HTML(display(source_image, dr_list[idx], st_list[idx]).to_html5_video())

In [157]:
idx+=1

In [158]:
HTML(display(source_image, dr_list[idx], re_list[idx]).to_html5_video())

In [159]:
HTML(display(source_image, dr_list[idx], st_list[idx]).to_html5_video())


In [160]:
idx+=1

In [161]:
HTML(display(source_image, dr_list[idx], re_list[idx]).to_html5_video())

In [162]:
HTML(display(source_image, dr_list[idx], st_list[idx]).to_html5_video())


In [163]:
idx+=1

In [164]:
HTML(display(source_image, dr_list[idx], re_list[idx]).to_html5_video())

In [165]:
HTML(display(source_image, dr_list[idx], st_list[idx]).to_html5_video())


> tennis

In [85]:
driving_video=[(plt.imread(im)) for im in glob(os.path.join(train_save_dir, '100080#tennis_1.mp4', '*'))]

In [86]:
predictions = make_animation(source_image, driving_video, generator, 
                             region_predictor, avd_network, animation_mode='standard')#animation_mode='avd')

#save resulting video
# imageio.mimsave('sample/ironman.mp4', [img_as_ubyte(frame) for frame in predictions])
#video can be downloaded from /content folder



HTML(display(source_image, driving_video, predictions).to_html5_video())

100%|██████████| 70/70 [00:02<00:00, 28.27it/s]


In [87]:
predictions = make_animation(source_image, driving_video, generator, 
                             region_predictor, avd_network, animation_mode='relative')#animation_mode='avd')

#save resulting video
# imageio.mimsave('sample/ironman.mp4', [img_as_ubyte(frame) for frame in predictions])
#video can be downloaded from /content folder



HTML(display(source_image, driving_video, predictions).to_html5_video())

100%|██████████| 70/70 [00:02<00:00, 26.04it/s]


In [88]:
# for_save=display(source_image, driving_video, predictions, save=True)
# imageio.mimsave('sample/iu_tennis.mp4', [img_as_ubyte(frame) for frame in for_save])

### Other

In [89]:
category_idx=47
train_anno_ex_dance_dir=os.path.join(train_anno_dir, os.listdir(train_anno_dir)[category_idx])
train_image_ex_dance_dir=os.path.join(train_image_dir, os.listdir(train_image_dir)[category_idx])

In [90]:
(driving_video,original_video, 
 original_annotations,new_annotations,bboxes)=crop_video_using_path(train_image_ex_dance_dir, 
                                                          train_anno_ex_dance_dir, return_original=True, masking=True)

driving_video = [resize(pad_white(frame[..., :3]), (384, 384)) for frame in driving_video]

In [91]:
url='https://image.shutterstock.com/image-photo/back-view-man-walking-pointing-600w-1337451158.jpg'
os.system("curl " + url + "> tobigs_test/test.png")
source_image=imageio.imread('tobigs_test/test.png')
source_image=rgba2rgb(source_image)
source_image = resize(pad_white(source_image[..., :3]), (384,384))


In [92]:
predictions = make_animation(source_image, driving_video, generator, 
                             region_predictor, avd_network, animation_mode='standard')#animation_mode='avd')

#save resulting video
# imageio.mimsave('sample/ironman.mp4', [img_as_ubyte(frame) for frame in predictions])
#video can be downloaded from /content folder



HTML(display(source_image, driving_video, predictions).to_html5_video())

100%|██████████| 65/65 [00:02<00:00, 27.46it/s]


In [93]:
predictions = make_animation(source_image, driving_video, generator, 
                             region_predictor, avd_network, animation_mode='relative')#animation_mode='avd')

#save resulting video
# imageio.mimsave('sample/ironman.mp4', [img_as_ubyte(frame) for frame in predictions])
#video can be downloaded from /content folder



HTML(display(source_image, driving_video, predictions).to_html5_video())

100%|██████████| 65/65 [00:02<00:00, 27.92it/s]


## Using DAVIS-DATASET

In [94]:
from preprocessing_davis import crop_video_using_path

In [95]:
from preprocessing_davis import *

In [96]:
from preprocessing_davis import display_video
from preprocessing_davis import mask_image
from preprocessing_davis import bbox2squared

In [97]:
category_idx=30
train_anno_ex_dance_dir=os.path.join(train_anno_dir, os.listdir(train_anno_dir)[category_idx])
train_image_ex_dance_dir=os.path.join(train_image_dir, os.listdir(train_image_dir)[category_idx])

In [98]:
(driving_video,original_video, 
 original_annotations,new_annotations,bboxes)=crop_video_using_path(train_image_ex_dance_dir, 
                                                          train_anno_ex_dance_dir, return_original=True, masking=True)

driving_video = [resize(pad_white(frame[..., :3]), (384, 384)) for frame in driving_video]

#### 1. driving video에 object의 크기를 맞췄을 때(즉, source image의 object에 대한 annotation이 driving video와 동일)

1. video 내 mask 부분의 값을 0으로, 나머지는 1로.
2. video 내에 mask 더하기(단, 나머지의 값은 0으로)

> 문제  
1. 학습 자체를 384x384로 했기 때문에 그 이상의 object는 삽입 불가능(잘릴 것)  
2. 아래의 test 함수는 우선 강제로 video의 annotation을 제거했기 때문에 픽셀 간 이격이 생길 수 있음


#### video 내에 object 삽입

In [ ]:
def synthesize(original_video, predictions, annotations, new_annotations, bboxes):
    new_video=[]
    i=0

    for frame in range(len(original_video)):
        frame_only_background=mask_image(original_video[frame], annotations[frame], reverse=True)
        #frame_onlybboxes[frame]

        ymin, ymax, xmin, xmax=bboxes[frame][2],bboxes[frame][3],bboxes[frame][0],bboxes[frame][1]

        part=frame_only_background[ymin:ymax, xmin:xmax]

        pixel_mean=new_annotations[frame].mean(axis=2)
        mask_remover=np.broadcast_to(pixel_mean[..., np.newaxis], pixel_mean.shape+(3,)).astype('uint8')

        part=part*(mask_remover==0).astype(int)

        a=mask_image(predictions[frame], new_annotations[frame])
        a[a==255]=0

        a=(a*255).astype(int)

        part=part+a

        frame_only_background[ymin:ymax, xmin:xmax]=part

        new_video.append(frame_only_background)
    return new_video

### Other

In [ ]:
category_idx=47
train_anno_ex_dance_dir=os.path.join(train_anno_dir, os.listdir(train_anno_dir)[category_idx])
train_image_ex_dance_dir=os.path.join(train_image_dir, os.listdir(train_image_dir)[category_idx])

In [88]:
(driving_video,original_video, 
 original_annotations,new_annotations,bboxes)=crop_video_using_path(train_image_ex_dance_dir, 
                                                          train_anno_ex_dance_dir, return_original=True, masking=True)

driving_video = [resize(pad_white(frame[..., :3]), (384, 384)) for frame in driving_video]

In [89]:
url='https://image.shutterstock.com/image-photo/back-view-man-walking-pointing-600w-1337451158.jpg'
os.system("curl " + url + "> tobigs_test/test.png")
source_image=imageio.imread('tobigs_test/test.png')
source_image=rgba2rgb(source_image)
source_image = resize(pad_white(source_image[..., :3]), (384,384))


In [91]:
predictions = make_animation(source_image, driving_video, generator, 
                             region_predictor, avd_network, animation_mode='standard')

#save resulting video
# imageio.mimsave('sample/ironman.mp4', [img_as_ubyte(frame) for frame in predictions])
#video can be downloaded from /content folder



HTML(display(source_image, driving_video, predictions).to_html5_video())

100%|██████████| 65/65 [00:02<00:00, 28.24it/s]


In [92]:
predictions = make_animation(source_image, driving_video, generator, 
                             region_predictor, avd_network, animation_mode='relative')

#save resulting video
# imageio.mimsave('sample/ironman.mp4', [img_as_ubyte(frame) for frame in predictions])
#video can be downloaded from /content folder



HTML(display(source_image, driving_video, predictions).to_html5_video())

100%|██████████| 65/65 [00:02<00:00, 27.73it/s]


### Other

In [93]:
category_idx=47
train_anno_ex_dance_dir=os.path.join(train_anno_dir, os.listdir(train_anno_dir)[category_idx])
train_image_ex_dance_dir=os.path.join(train_image_dir, os.listdir(train_image_dir)[category_idx])

In [94]:
(driving_video,original_video, 
 original_annotations,new_annotations,bboxes)=crop_video_using_path(train_image_ex_dance_dir, 
                                                          train_anno_ex_dance_dir, return_original=True, masking=True)

driving_video = [resize(pad_white(frame[..., :3]), (384, 384)) for frame in driving_video]

In [95]:
url='https://image.shutterstock.com/image-photo/back-view-man-walking-pointing-600w-1337451158.jpg'
os.system("curl " + url + "> tobigs_test/test.png")
source_image=imageio.imread('tobigs_test/test.png')
source_image=rgba2rgb(source_image)
source_image = resize(pad_white(source_image[..., :3]), (384,384))


In [97]:
predictions = make_animation(source_image, driving_video, generator, 
                             region_predictor, avd_network, animation_mode='standard')

#save resulting video
# imageio.mimsave('sample/ironman.mp4', [img_as_ubyte(frame) for frame in predictions])
#video can be downloaded from /content folder



HTML(display(source_image, driving_video, predictions).to_html5_video())

100%|██████████| 65/65 [00:02<00:00, 28.86it/s]


In [98]:
HTML(display_video(synthesize(original_video, predictions, original_annotations, new_annotations, bboxes)).to_html5_video())

In [99]:
url='https://upload.wikimedia.org/wikipedia/commons/thumb/9/93/Blue_person_pictogram.svg/langko-450px-Blue_person_pictogram.svg.png'
os.system("curl " + url + "> tobigs_test/test.png")
source_image=imageio.imread('tobigs_test/test.png')
source_image=rgba2rgb(source_image)
source_image = resize(pad_white(source_image[..., :3]), (384,384))


In [100]:
predictions = make_animation(source_image, driving_video, generator, 
                             region_predictor, avd_network, animation_mode='standard')

#save resulting video
# imageio.mimsave('sample/ironman.mp4', [img_as_ubyte(frame) for frame in predictions])
#video can be downloaded from /content folder



HTML(display(source_image, driving_video, predictions).to_html5_video())

100%|██████████| 65/65 [00:02<00:00, 25.88it/s]


In [102]:
HTML(display_video(synthesize(original_video, predictions, original_annotations, new_annotations, bboxes)).to_html5_video())